# Floc Collisions Model 

This notebook does the following: 
1. Creates particles in the size range of `0.1 - 100um`
2. Calculates collision frequency functions using the `long-range` and `short-range` models
3. Find the dominant CFF mechanisms
4. Plots all the figures

## Getting Started

To get started, you'll want to install the following packages:

* numpy `conda install numpy`
* pandas `conda install pandas`
* itertools 
* math
* plotly `conda install plotly`

*The last cell contains the function that generates a CFF plot based the user specified `G-value`,`Density`,`Temperature`, and `Size Ranges`.*  **Note: The variable have to be entered in that order**

### Import Dependencies

In [7]:
import pandas as pd
import numpy as np
from itertools import product
import math
import plotly.express as px
import plotly.graph_objects as go

### Create Particle Sizes

In [2]:
# Creates a list of particle sizes
sizes = np.geomspace(0.1, 100, 100, endpoint=True)
# Create a data frame with 2 columns that contains all combinations of particle sizes 
ds = pd.DataFrame(list(product(sizes, sizes)), columns=['di', 'dj'])
# Remove duplicate rows so we don't double count
a = np.sort(ds.to_numpy(), axis=1)
ds = ds.groupby([a[:, 0], a[:, 1]], as_index=False, sort=False).first()

### Create a function to calculate short range collision frequency functions

#### Function for creating a discrete color scale

In [3]:
def discrete_colorscale(bvals, clrs):
    """
    bvals - list of values bounding intervals/ranges of interest
    colors - list of rgb or hex colorcodes for values in [bvals[k], bvals[k+1]],0<=k < len(bvals)-1
    returns the plotly  discrete colorscale
    """
    if len(bvals) != len(clrs) + 1:
        raise ValueError('len(boundary values) should be equal to  len(colors)+1')
    bvals = sorted(bvals)
    nvals = [(v - bvals[0]) / (bvals[-1] - bvals[0]) for v in bvals]  # normalized values

    dcolorscale = []  # discrete colorscale
    for k in range(len(clrs)):
        dcolorscale.extend([[nvals[k], clrs[k]], [nvals[k + 1], clrs[k]]])
    return dcolorscale


# Scale Values
rng = [0, 1, 2, 3]
# Scale Colors
colors = ["rgb(4,106,56)", "rgb(0,51,160)", "rgb(191, 87, 0)"]
# Color Scale
dcolorsc = discrete_colorscale(rng, colors)

#### Function to calculate short-range collision frequency functions

In [4]:
def cff(gv=20,pp=1.2,T=20,ds=ds):
        
    # Arguments
    # gv = G-value [1/s]; pp = particle density [g/cm3]; T = temperature [C]; ds = particle sizes

    # Calculate Constants
    ds = ds.copy()
    pl = (1 - (T + 288.9414) / (508929.2 * (T + 68.12963)) * (T - 3.9863) ** 2)  # liquid density
    vis = (math.exp((-3.7188 + (578.919 / (-137.546 + (T + 273.15)))))) / 100  # viscosity
    T = T + 273.15  # temperature in K
    kb = 1.38E-16  # Boltzmann's constant
    ham = 3E-13  # Hamakar's constant
    
    ###### Calculate long range forces
    
    # Creates a column for the long range shear collisions
    ds['shr_beta'] = (1 / 6) * gv * ((ds.di / 10 ** 4) + (ds.dj / 10 ** 4)) ** 3
    # Creates a column for the long range differential settling collisions
    ds['ds_beta'] = ((math.pi * 981) / (72 * vis)) * (pp - pl) * (
            ((ds.di / 10 ** 4) + (ds.dj / 10 ** 4)) ** 3) * abs((ds.di / 10 ** 4) - (ds.dj / 10 ** 4))
    # Creates a column for the long range Brownian motion collisions
    ds['bm_beta'] = ((2 * kb * T) / (3 * vis)) * ((1 / (ds.di / 10 ** 4)) + (1 / (ds.dj / 10 ** 4))) * (
            (ds.di / 10 ** 4) + (ds.dj / 10 ** 4))
    
    ###### Calculate short range forces
    
    # Split data frame into sizes and long range collisions
    d_sizes = ds[['di', 'dj']].copy()
    df = ds.copy()
    
    # Determine which particle is larger
    d_sizes['larger'] = d_sizes.max(axis=1)
    # Calculates lambda
    d_sizes['lamb'] = ((d_sizes.min(axis=1)) / (d_sizes.max(axis=1)))
    d_sizes.replace(np.Inf, 1, inplace=True)
    
    # Short Range Brownian
    
    ## Estimate polynomial function parameters from Han and Lawler 1992
    d_sizes['a'] = (0.00116 + 0.17909 * (d_sizes.larger ** (-1.23309))) ** (-1 / -44.38899)
    d_sizes['b'] = -0.42653 - (0.85932 * (1 - np.exp(-(d_sizes['larger'] / 0.3384)))) - (
            0.46261 * (1 - np.exp(-(d_sizes['larger'] / 9.44541))))
    d_sizes['c'] = 0.23856 + (1.34712 * (1 - np.exp(-(d_sizes['larger'] / 0.37939)))) + (
            0.80882 * (1 - np.exp(-(d_sizes['larger'] / 10.46041))))
    d_sizes['d'] = -0.02451 - (0.65901 * (1 - np.exp(-(d_sizes['larger'] / 0.40195)))) - (
            0.41971 * (1 - np.exp(-(d_sizes['larger'] / 11.02823))))
    ## Calculate brownian motion adjustment factor
    d_sizes['b_brwn'] = d_sizes.a + (d_sizes.b * d_sizes.lamb) + (d_sizes.c * d_sizes.lamb ** 2) + (
            d_sizes.d * d_sizes.lamb ** 3)
    ## Creates a column for the short range Brownian motion collisions
    d_sizes['shrt_brwn'] = d_sizes.b_brwn * df.bm_beta
    ## Remove Operations columns
    d_sizes = d_sizes.drop(columns=['a', 'b', 'c', 'd', 'b_brwn'])
    
    # Short Range Shear
    
    ## Estimate polynomial function parameters from Han and Lawler 1992
    d_sizes['Ha'] = np.log10((ham / (18 * math.pi * vis * ((d_sizes.larger / 10000) ** 3) * gv)))
    d_sizes['a'] = (-0.1188 * d_sizes.Ha ** 2) + (0.1949 * d_sizes.Ha) - 1.1231
    d_sizes['b'] = (0.4446 * d_sizes.Ha ** 2) - (0.1675 * d_sizes.Ha) + 2.1099
    d_sizes['c'] = (-0.4883 * d_sizes.Ha ** 2) + (0.5982 * d_sizes.Ha) - 1.695
    d_sizes['d'] = (0.183 * d_sizes.Ha ** 2) - (0.3854 * d_sizes.Ha) + 0.6122
    ## Calculate Shear adjustment factor
    d_sizes['b_shr'] = (8 / (1 + d_sizes.lamb) ** 3) * 10 ** (
            d_sizes.a + (d_sizes.b * d_sizes.lamb) + (d_sizes.c * d_sizes.lamb ** 2) + (d_sizes.d * d_sizes.lamb ** 3))
    ## Creates a column for the short range Shear collisions
    d_sizes['shrt_shear'] = d_sizes.b_shr * df.shr_beta
    ## Remove Operations columns
    d_sizes = d_sizes.drop(columns=['a', 'b', 'c', 'd', 'Ha', 'b_shr'])
    
    # Short Range Settling
    
    ## Estimate polynomial function parameters from Han and Lawler 1992
    d_sizes['ng'] = np.log10(((48 * ham) / (math.pi * 981 * (pp - pl) * (d_sizes.larger / 10000) ** 4)))
    d_sizes['a'] = (0.0211 * d_sizes.ng ** 2) + (0.5006 * d_sizes.ng) + (- 0.8402)
    d_sizes['b'] = (-0.0381 * d_sizes.ng ** 2) + (-0.9331 * d_sizes.ng) + 0.4231
    d_sizes['c'] = (0.0253 * d_sizes.ng ** 2) + (1.1302 * d_sizes.ng) + (- 1.0683)
    d_sizes['d'] = (0.0012 * d_sizes.ng ** 2) + (-0.4299 * d_sizes.ng) + 0.9298
    ## Calculate settling adjustment factor
    d_sizes['b_ds'] = 10 ** (d_sizes.a + (d_sizes.b * d_sizes.lamb) + (d_sizes.c * d_sizes.lamb ** 2) + (
            d_sizes.d * d_sizes.lamb ** 3))
    ## Creates a column for the short range settling collisions
    d_sizes['shrt_settle'] = d_sizes.b_ds * df.ds_beta
    ## Remove Operations columns
    d_sizes = d_sizes.drop(columns=['a', 'b', 'c', 'd', 'ng', 'larger', 'lamb'])
        
    # Identify Dominant Mechanisms

    df = pd.concat([d_sizes, df], axis=1)
    df = df[['di', 'dj', 'shrt_brwn', 'shrt_shear', 'shrt_settle']].copy()
    d_sizes = ds[['di', 'dj']].copy()  # Creates a data frame of sizes only
    df = df.drop(columns=['di', 'dj'])  # Removing sizes for analyses
    df['mech'] = df.idxmax(axis=1)  # Create a column that shows which mechanism is dominant
    
    # Caluclate total CFF
    df['sum'] = df.sum(axis=1) 
    
    # code values for creating a plot
    df.loc[df['mech'] == 'shrt_brwn', 'max'] = '1'
    df.loc[df['mech'] == 'shrt_shear', 'max'] = '2'
    df.loc[df['mech'] == 'shrt_settle', 'max'] = '3'
    
    # Replace column index results with labels
    df.replace("shrt_shear", "Shear", inplace=True)
    df.replace("shrt_settle", "Differential Settling", inplace=True)
    df.replace("shrt_brwn", "Brownian", inplace=True)
    
    # Final Data Frame
    df = pd.concat([d_sizes, df], axis=1)

    # Calculate Fraction of mechanism
    df['shrp'] = (df['shrt_shear']/df['sum'])*100
    df['brwnp'] = (df['shrt_brwn']/df['sum'])*100
    df['diffp'] = (df['shrt_settle']/df['sum'])*100
    
    # Plot it
    
    # Create contour plot figure
    fig = go.Figure(data=go.Contour(
        z=df['max'],
        x=df['di'],
        y=df['dj'],
        contours=dict(
            start=1,
            end=3,
            size=1,
            coloring='heatmap',
        ),
        opacity=0.92,
        connectgaps=False,
        line=dict(smoothing=0.5, width=0),
        colorbar=dict(
            title="Mechanism",
            titleside="top",
            tickmode="array",
            tickvals=[1, 2, 3],
            ticktext=["Brownian", "Shear", "Settling"],
            ticklen=0,
            tickangle=-90
        ),
        hoverongaps=False,
        colorscale=dcolorsc,
        text=df['mech'].values,
        customdata=df,
        hovertemplate="d\u1D62: %{x:.2f}\u00B5m" +
                      '<br>' +
                      "d\u2C7C: %{y:.2f}\u00B5m" +
                      "<br>"
                      +
                      "Mechanism: %{text}" +
                      "<br>" + "<br>"
                      +
                      "Total: %{customdata[6]:.2e} cm\u00B3/s"
                      +
                      "<br>"
                      +
                      "Shear: %{customdata[8]:.1f}%"
                      +
                      "<br>"
                      +
                      "Diff. Settling: %{customdata[10]:.1f}%"
                      +
                      "<br>"
                      +
                      "Brownian: %{customdata[9]:.1f}%"
                      "<extra></extra>",
            ))

    tickvals = np.concatenate(
            (np.arange(0.1, 1.0, 0.1), np.arange(1.0, 10, 1), np.arange(10.0, 100, 10), np.arange(100.0, 1100, 100),))
    ticktext = [str(val) if val in [0.1, 1, 10, 100] else '' for val in tickvals]

    fig.update_xaxes(type="log",
                     title='d\u1D62 [\u00B5m]',
                     titlefont=dict(size=20),
                     tickfont=dict(size=15),
                     ticks="outside",
                     tickvals=tickvals,
                     ticktext=ticktext,
                     automargin=False,
                     color='black', linecolor='black', mirror=True)

    fig.update_yaxes(type="log",
                     title='d\u2C7C [\u00B5m]',
                     titlefont=dict(size=20),
                     tickfont=dict(size=15),
                     ticks="outside",
                     tickvals=tickvals,
                     ticktext=ticktext,
                     automargin=False, color='black', linecolor='black', mirror=True)

    fig.update_layout(title={
        'text': "Han & Lawler Model",
        'y': 0.9,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
        titlefont=dict(size=30)
    )

    fig.show()
    
    return df

# PLOT GENERATION

To use the function:
* Assign the function to a variable
    * Example: data = `cff(...`
* Enter the boundary condintions of your model in the order of:
    * `G-value [1/s]`
    * `Particle density [g/cm3]`
    * `Temperature [C]`
    * `Size Range` = ds (from cell #2 above)

In [5]:
data = cff(20,1.2,20,ds)